In [48]:
# http://overpass-turbo.eu/
# https://download.geofabrik.de/europe/hungary.html
HUNGARY_LOC = [47.32,20.0589]
BUDAPEST_LOC = [47.496288, 19.044552]
import pandas as pd
import requests
import json
overpass_url = "http://overpass-api.de/api/interpreter"
overpass_query = """
[out:json];
area["ISO3166-1"="HU"][admin_level=2];
(node["tourism"="museum"](area);
 way["tourism"="museum"](area);
 rel["tourism"="museum"](area);
);
out center;
"""
response = requests.get(overpass_url, 
                        params={'data': overpass_query})
data = response.json()

In [3]:
import numpy as np
import matplotlib.pyplot as plt
# Collect coords into list

lts = []
lns = []
nms = [] 
for element in data['elements']:
  if element['type'] == 'node':
    lns.append(element['lon'])
    lts.append(element['lat'])
    try:
        nms.append(element['tags']['name'])
    except:
        print(element)
        nms.append("Unknown")


{'type': 'node', 'id': 871669036, 'lat': 47.7452949, 'lon': 18.1384013, 'tags': {'tourism': 'museum'}}
{'type': 'node', 'id': 1085803923, 'lat': 45.9907361, 'lon': 18.6908238, 'tags': {'tourism': 'museum'}}
{'type': 'node', 'id': 1349489431, 'lat': 48.0956667, 'lon': 20.7851962, 'tags': {'addr:city': 'Miskolc', 'addr:housenumber': '28', 'addr:postcode': '3529', 'addr:street': 'Görgey Artúr utca', 'fee': 'yes', 'tourism': 'museum'}}
{'type': 'node', 'id': 1449747283, 'lat': 47.216437, 'lon': 20.74896, 'tags': {'tourism': 'museum'}}
{'type': 'node', 'id': 1595931510, 'lat': 47.0006634, 'lon': 21.4883826, 'tags': {'tourism': 'museum'}}
{'type': 'node', 'id': 1620261094, 'lat': 47.3895932, 'lon': 16.5385461, 'tags': {'tourism': 'museum', 'wheelchair': 'yes'}}
{'type': 'node', 'id': 1928856586, 'lat': 47.5926821, 'lon': 19.8529249, 'tags': {'tourism': 'museum'}}
{'type': 'node', 'id': 1975866185, 'lat': 47.5810844, 'lon': 18.3991081, 'tags': {'addr:postcode': '2800', 'addr:street': 'Szent B

In [33]:
df = pd.DataFrame(
    {'Lat': lts,
     'Long': lns,
     'Name': nms
    })

In [5]:
import folium
from folium import Choropleth, Circle, Marker
from folium.plugins import HeatMap, MarkerCluster

In [6]:
# Create a map
m1 = folium.Map(location=[47.32,20.0589], tiles='cartodbpositron', zoom_start=7)

# Add points to the map
for idx, row in df.iterrows():
    Marker([row['Lat'], row['Long']],popup=row['Name']).add_to(m1)

# Display the map
m1

In [6]:
m2 = folium.Map(location=[47.32,20.0589], tiles='cartodbpositron', zoom_start=7)
HeatMap(data=df[['Lat', 'Long']], radius=15).add_to(m2)
m2

In [7]:
## Day 2 getting hungary county data and budapest district data and making a Choropleth map

In [72]:
# getting the districts of budapest
import osmium
import shapely.wkb
import pandas as pd
import geopandas as gpd

region = "hungary"

def merge_two_dicts(x, y):
    z = x.copy()   # start with keys and values of x
    z.update(y)    # modifies z with keys and values of y
    return z

class AdminAreaHandler(osmium.SimpleHandler):
    def __init__(self):
        osmium.SimpleHandler.__init__(self)

        self.areas = []
        self.wkbfab = osmium.geom.WKBFactory()

    def area(self, a):            
        if  "admin_level" in a.tags:

            wkbshape = self.wkbfab.create_multipolygon(a)
            shapely_obj = shapely.wkb.loads(wkbshape, hex=True)
            
            area = { "id": a.id, "geo": shapely_obj }
            area = merge_two_dicts(area, a.tags)
            
            self.areas.append(area)
        
handler = AdminAreaHandler()

# path to file to local drive
# download from https://download.geofabrik.de/index.html
osm_file = "hungary-latest.osm.pbf"

# start data file processing
handler.apply_file(osm_file, locations=True, idx='flex_mem')

df1 = pd.DataFrame(handler.areas)
gdf = gpd.GeoDataFrame(df1, geometry="geo")
gdf

id                                                geo admin_level  \
0     61395202  MULTIPOLYGON (((22.37851 48.25962, 22.37860 48...           9   
1       219047  MULTIPOLYGON (((16.44957 47.65444, 16.44959 47...           8   
2       226953  MULTIPOLYGON (((18.79674 47.54778, 18.80085 47...           8   
3       226951  MULTIPOLYGON (((18.76212 47.50128, 18.76642 47...           8   
4       226955  MULTIPOLYGON (((18.77939 47.56465, 18.78253 47...           8   
...        ...                                                ...         ...   
4431    443969  MULTIPOLYGON (((19.02376 47.49562, 19.02376 47...           9   
4432   5572621  MULTIPOLYGON (((19.00853 47.50997, 19.00865 47...          10   
4433   5613881  MULTIPOLYGON (((19.00521 47.48378, 19.00532 47...          10   
4434  31185331  MULTIPOLYGON (((18.92690 47.52224, 18.92828 47...           8   
4435    443991  MULTIPOLYGON (((18.92690 47.52224, 18.92828 47...           9   

                      boundary      koatuu  \
0               administrative  2120488003   
1               administrative         NaN   
2               administrative         NaN   
3               administrative         NaN   
4               administrative         NaN   
...                        ...         ...   
4431            administrative         NaN   
4432            administrative         NaN   
4433            administrative         NaN   
4434  religious_administration         NaN   
4435            administrative         NaN   

                                         name        name:en    name:hu  \
0                                 Мале Попово    Male Popovo  Papitanya   
1                            Gemeinde Ritzing            NaN        NaN   
2                                       Telki            NaN        NaN   
3                                        Páty            NaN        NaN   
4                                    Budajenő            NaN        NaN   
...                                       ...            ...        ...   
4431                               I. kerület   1st district        NaN   
4432                           Krisztinaváros            NaN        NaN   
4433                               Németvölgy            NaN        NaN   
4434  Budahegyvidéki Evangélikus Egyházközség            NaN        NaN   
4435                             XII. kerület  12th district        NaN   

     name:prefix       name:ru  ... old_name:vi old_name:vi:-2011-12-31  \
0           село  Малое Попово  ...         NaN                     NaN   
1            NaN           NaN  ...         NaN                     NaN   
2            NaN           NaN  ...         NaN                     NaN   
3            NaN           NaN  ...         NaN                     NaN   
4            NaN           NaN  ...         NaN                     NaN   
...          ...           ...  ...         ...                     ...   
4431         NaN           NaN  ...         NaN                     NaN   
4432         NaN           NaN  ...         NaN                     NaN   
4433         NaN           NaN  ...         NaN                     NaN   
4434         NaN           NaN  ...         NaN                     NaN   
4435         NaN           NaN  ...         NaN                     NaN   

     timezone end_date ref:nuts:1 name:gr name:grc name:hyw is_in alt_name:hu  
0         NaN      NaN        NaN     NaN      NaN      NaN   NaN         NaN  
1         NaN      NaN        NaN     NaN      NaN      NaN   NaN         NaN  
2         NaN      NaN        NaN     NaN      NaN      NaN   NaN         NaN  
3         NaN      NaN        NaN     NaN      NaN      NaN   NaN         NaN  
4         NaN      NaN        NaN     NaN      NaN      NaN   NaN         NaN  
...       ...      ...        ...     ...      ...      ...   ...         ...  
4431      NaN      NaN        NaN     NaN      NaN      NaN   NaN         NaN  
4432      NaN      NaN        NaN     NaN   

In [17]:
bud = gdf.loc[gdf['admin_level'] == "9"]

In [30]:
bud = bud[bud.apply(lambda r: r.str.contains('Budapest', case=False).any(), axis=1)]

In [40]:
gdf1 = gpd.GeoDataFrame(
    df, geometry=gpd.points_from_xy(df.Long, df.Lat)
)

In [52]:
budapest_museums = gpd.sjoin(gdf1, bud)

In [69]:
plot_dict = budapest_museums.name.value_counts()

In [65]:
districts = bud[["name", "geo"]].set_index("name")

In [49]:
m_6 = folium.Map(location=BUDAPEST_LOC, tiles='cartodbpositron', zoom_start=12)

In [70]:
m_6 = folium.Map(location=BUDAPEST_LOC, tiles='cartodbpositron', zoom_start=11)
# Add a choropleth map to the base map
Choropleth(geo_data=districts.__geo_interface__, 
           data=plot_dict, 
           key_on="feature.id", 
           fill_color='YlGnBu', 
           legend_name='Museums Budapest'
          ).add_to(m_6)

# Display the map
m_6

In [93]:
megye = gdf.loc[gdf['admin_level'] == "6"]
megye = megye[megye['name'].str.contains("vármegye")]
megye_museums = gpd.sjoin(gdf1, megye)
plot_dict = megye_museums.name.value_counts()
districts = megye[["name", "geo"]].set_index("name")

In [94]:
m_6 = folium.Map(location=HUNGARY_LOC, tiles='cartodbpositron', zoom_start=7)
# Add a choropleth map to the base map
Choropleth(geo_data=districts.__geo_interface__, 
           data=plot_dict, 
           key_on="feature.id", 
           fill_color='YlGnBu', 
           legend_name='Museums Hungary'
          ).add_to(m_6)

# Display the map
m_6

In [95]:
megye = gdf.loc[gdf['admin_level'] == "7"]
megye = megye[megye['name'].str.contains("járás")]
megye_museums = gpd.sjoin(gdf1, megye)
plot_dict = megye_museums.name.value_counts()
districts = megye[["name", "geo"]].set_index("name")

In [96]:
m_6 = folium.Map(location=HUNGARY_LOC, tiles='cartodbpositron', zoom_start=7)
# Add a choropleth map to the base map
Choropleth(geo_data=districts.__geo_interface__, 
           data=plot_dict, 
           key_on="feature.id", 
           fill_color='YlGnBu', 
           legend_name='Museums Hungary'
          ).add_to(m_6)

# Display the map
m_6